<h3> Step 1: Data Extraction and Data Processing </h3>

In [1]:
import pandas as pd
import requests
import pandas as pd
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
df_list = pd.read_html(url)
dfCanada = df_list[0]
dfCanada = dfCanada.mask(dfCanada["Borough"] == "Not assigned")
dfCanada = dfCanada.dropna(subset = ["Borough"])
dfCanada = dfCanada.reset_index(drop =True)
dfCanada.head()

Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [3]:
listPostalCode = dfCanada["Postal Code"].unique()
coord = pd.DataFrame(pd.read_csv("Geospatial_Coordinates.csv"))
tabLat = []
tabLon = []
for i in listPostalCode:
    lat = float(coord.where(coord["Postal Code"] == i).dropna()["Latitude"])
    lon = float(coord.where(coord["Postal Code"] == i).dropna()["Longitude"])
    tabLat.append(lat)
    tabLon.append(lon)
dfCanada["Latitude"]= tabLat
dfCanada["Longitude"]= tabLon
dfCanada.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [4]:
#Foursquare API credentials necessary to pull requests
CLIENT_ID = '5ATIS4WC1M2CRJ1OF3XIV4R05BNFZDEZNIWXNDP42HHTCR4E' # your Foursquare ID
CLIENT_SECRET = 'MUETT0KTMZZHPPYV0VC1LZ3QYMMASLKGA5ZF2VRLW4N5VDAU' # your Foursquare Secret
ACCESS_TOKEN = 'EVSJNRTM1CHDIMX2B11DEBYVQF0ULLAZMQNEE5PTXQ0ODLGU' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 25
dfCanada=dfCanada.drop("Postal Code" ,axis = 1)

<h3> Useful functions and further work for neighborhood clustering </h3>

In [5]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
#This function was borrowed from an IBM lab    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [78]:
from geopy.geocoders import Nominatim
import numpy as np # library to handle data in a vectorized manner

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')
address = 'Toronto, Ca'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

usage: conda-script.py [-h] [-V] command ...
conda-script.py: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab


Libraries imported.


usage: conda-script.py [-h] [-V] command ...
conda-script.py: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab


In [79]:
toronto_venues = getNearbyVenues(names=dfCanada['Neighbourhood'],
                                   latitudes=dfCanada['Latitude'],
                                   longitudes=dfCanada['Longitude']
                                  )
toronto_venues.head()

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0         Parkwoods               43.753259               -79.329656   
1         Parkwoods               43.753259               -79.329656   
2         Parkwoods               43.753259               -79.329656   
3         Parkwoods               43.753259               -79.329656   
4  Victoria Village               43.725882               -79.315572   

                               Venue  Venue Latitude  Venue Longitude  \
0                    Brookbanks Park       43.751976       -79.332140   
1                    Brookbanks Pool       43.751389       -79.332184   
2                      Variety Store       43.751974       -79.333114   
3  Corrosion Service Company Limited       43.752432       -79.334661   
4             Victoria Village Arena       43.723481       -79.315635   

               Venue Category  
0                        Park  
1                        Pool  
2           Food & Drink Shop  
3  Construction & Landscaping  
4                Hockey Arena

In [80]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighbourhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighbourhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Airport  Airport Food Court  \
0         Parkwoods                  0        0                   0   
1         Parkwoods                  0        0                   0   
2         Parkwoods                  0        0                   0   
3         Parkwoods                  0        0                   0   
4  Victoria Village                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0            0           0                    0   
1             0            0           0                    0   
2             0            0           0                    0   
3             0            0           0                    0   
4             0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Basketball Stadium  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                   0         0           0                   0          0   
1                   0         0           0                   0          0   
2                   0         0           0                   0          0   
3                   0         0           0                   0          0   
4                   0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  Breakfast Spot  \
0       0           0              0          0         0               0   
1       0           0              0          0         0               0   
2       0           0              0          0         0               0   
3       0           0              0          0         0               0   
4       0           0              0          0         0               0   

   Brewery  Bridal Shop  Bubble Tea Shop  Burger Joint  Burrito Place  \
0        0            0                0             0              0   
1        0            0                0             0              0   
2        0            0                0             0              0   
3        0            0                0             0              0   
4        0            0                0             0              0   

   Bus Line  Bus Station  Bus Stop  Business Service  Butcher  Café  \
0         0            0         0                 0        0     0   
1         0            0         0                 0        0     0   
2         0            0         0                 0        0     0   
3         0            0         0                 0        0     0   
4         0            0         0                 0        0     0   

   Cajun / Creole Restaurant  Camera Store  Candy

In [81]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]
num_top_venues = 10

indicators = ['st', 'nd', 'rd']
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped
# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue  \
0                                        Agincourt        Breakfast Spot   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North           Coffee Shop   
3                                  Bayview Village    Chinese Restaurant   
4                Bedford Park, Lawrence Manor East        Sandwich Place   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Latin American Restaurant        Clothing Store          Skating Rink   
1         Athletics & Sports              Pharmacy                   Gym   
2                       Bank        Ice Cream Shop             Pet Store   
3                       Bank                  Café   Japanese Restaurant   
4                Coffee Shop    Italian Restaurant                   Pub   

  5th Most Common Venue 6th Most Common Venue      7th Most Common Venue  \
0                Lounge           Yoga Studio         Dim Sum Restaurant   
1                   Pub          Dance Studio             Sandwich Place   
2           Pizza Place     Mobile Phone Shop  Middle Eastern Restaurant   
3           Yoga Studio    Dim Sum Restaurant         Falafel Restaurant   
4       Thai Restaurant        Breakfast Spot    Comfort Food Restaurant   

  8th Most Common Venue 9th Most Common Venue       10th Most Common Venue  
0           Escape Room     Electronics Store  Eastern European Restaurant  
1          Skating Rink           Coffee Shop                    Gastropub  
2            Restaurant         Deli / Bodega               Sandwich Place  
3           Escape Room     Electronics Store  Eastern European Restaurant  
4  Fast Food Restaurant             Juice Bar                   Restaurant

In [82]:
# set number of clusters
kclusters = 7

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[:] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 6, 1, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 6, 3, 1, 1, 1, 1,
       0, 1, 6, 1, 1, 6, 6, 1, 4, 1, 6, 1, 1, 1, 3, 1, 1, 6, 1, 1, 1, 6,
       1, 2, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 6, 1, 1, 1, 1, 1, 1,
       5, 1, 5, 1, 1, 1, 6, 6])

In [83]:
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
neighbourhoods_venues_sorted.head()

Cluster Labels                                    Neighbourhood  \
0               1                                        Agincourt   
1               1                           Alderwood, Long Branch   
2               1  Bathurst Manor, Wilson Heights, Downsview North   
3               1                                  Bayview Village   
4               1                Bedford Park, Lawrence Manor East   

  1st Most Common Venue      2nd Most Common Venue 3rd Most Common Venue  \
0        Breakfast Spot  Latin American Restaurant        Clothing Store   
1           Pizza Place         Athletics & Sports              Pharmacy   
2           Coffee Shop                       Bank        Ice Cream Shop   
3    Chinese Restaurant                       Bank                  Café   
4        Sandwich Place                Coffee Shop    Italian Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Skating Rink                Lounge           Yoga Studio   
1                   Gym                   Pub          Dance Studio   
2             Pet Store           Pizza Place     Mobile Phone Shop   
3   Japanese Restaurant           Yoga Studio    Dim Sum Restaurant   
4                   Pub       Thai Restaurant        Breakfast Spot   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0         Dim Sum Restaurant           Escape Room     Electronics Store   
1             Sandwich Place          Skating Rink           Coffee Shop   
2  Middle Eastern Restaurant            Restaurant         Deli / Bodega   
3         Falafel Restaurant           Escape Room     Electronics Store   
4    Comfort Food Restaurant  Fast Food Restaurant             Juice Bar   

        10th Most Common Venue  
0  Eastern European Restaurant  
1                    Gastropub  
2               Sandwich Place  
3  Eastern European Restaurant  
4                   Restaurant

In [84]:
toronto_merged = pd.merge(neighbourhoods_venues_sorted, dfCanada)

In [85]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [58]:
toronto_merged

Cluster Labels                                      Neighbourhood  \
0                1                                          Agincourt   
1                1                             Alderwood, Long Branch   
2                1    Bathurst Manor, Wilson Heights, Downsview North   
3                1                                    Bayview Village   
4                1                  Bedford Park, Lawrence Manor East   
5                1                                        Berczy Park   
6                1                        Birch Cliff, Cliffside West   
7                1       Brockton, Parkdale Village, Exhibition Place   
8                1  Business reply mail Processing Centre, South C...   
9                1  CN Tower, King and Spadina, Railway Lands, Har...   
10               6                                Caledonia-Fairbanks   
11               1              Canada Post Gateway Processing Centre   
12               1                                          Cedarbrae   
13               1                                 Central Bay Street   
14               1                                           Christie   
15               1                               Church and Wellesley   
16               1            Clarks Corners, Tam O'Shanter, Sullivan   
17               1    Cliffside, Cliffcrest, Scarborough Village West   
18               1                     Commerce Court, Victoria Hotel   
19               1                                         Davisville   
20               1                                   Davisville North   
21               1   Del Ray, Mount Dennis, Keelsdale and Silverthorn   
22               1                                          Don Mills   
23               1                                          Don Mills   
24               1  Dorset Park, Wexford Heights, Scarborough Town...   
25               1                                          Downsview   
26               1                                          Downsview   
27               1                                          Downsview   
28               1                                          Downsview   
29               1                       Dufferin, Dovercourt Village   
30               6      East Toronto, Broadview North (Old East York)   
31               1  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
32               1                       Fairview, Henry Farm, Oriole   
33               1             First Canadian Place, Underground city   
34               6    Forest Hill North & West, Forest Hill Road Park   
35               1                           Garden District, Ryerson   
36               1                                          Glencairn   
37               1                    Golden Mile, Clairlea, Oakridge   
38               1                  Guildwood, Morningside, West Hill   
39               1  Harbourfront East, Union Station, Toronto Islands   
40               1                      High Park, The Junction South   
41               1                                  Hillcrest Village   
42               6                                      Humber Summit   
43               3                                   Humberlea, Emery   
44               1                                 Humewood-Cedarvale   
45               1                     India Bazaar, The Beaches West   
46               1        Kennedy Park, Ionview, East Birchmount Park   
47               1          Kensington Market, Chinatown, Grange Park   
48               0  Kingsview Village, St. Phillips, Martin Grove ...   
49               1                   Lawrence Manor, Lawrence Heights   
50               6                                      Lawrence Park   
51               1                                            Leaside   
52               1                           Little Portugal, Trinity   
53               6                                     Malvern

In [59]:
toronto_merged.groupby(["Cluster Labels"]).count()

Neighbourhood  1st Most Common Venue  2nd Most Common Venue  \
Cluster Labels                                                                
0                           1                      1                      1   
1                          79                     79                     79   
2                           1                      1                      1   
3                           2                      2                      2   
4                           1                      1                      1   
5                           2                      2                      2   
6                          14                     14                     14   

                3rd Most Common Venue  4th Most Common Venue  \
Cluster Labels                                                 
0                                   1                      1   
1                                  79                     79   
2                                   1                      1   
3                                   2                      2   
4                                   1                      1   
5                                   2                      2   
6                                  14                     14   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                   1                      1   
1                                  79                     79   
2                                   1                      1   
3                                   2                      2   
4                                   1                      1   
5                                   2                      2   
6                                  14                     14   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                   1                      1   
1                                  79                     79   
2                                   1                      1   
3                                   2                      2   
4                                   1                      1   
5                                   2                      2   
6                                  14                     14   

                9th Most Common Venue  10th Most Common Venue  Borough  \
Cluster Labels                                                           
0                                   1                       1        1   
1                                  79                      79       79   
2                                   1                       1        1   
3                                   2                       2        2   
4                                   1                       1        1   
5                                   2                       2        2   
6                                  14                      14       14   

                Latitude  Longitude  
Cluster Labels                       
0                      1          1  
1                     79         79  
2                      1          1  
3                      2          2  
4                      1          1  
5                      2          2  
6                     14         14

In [ ]:
# From the clustering seen above it can be seen that the most common venues are very similar. 
# It was therefore decided to perform a second clustering but this time based on the most trending venues.
# And if a neughborhood has for number 1 trending plase a taiwanese restaurant then the neighborhood the most similar
#will be chosen as the best place
#If even after this analysis further anlysis is necessary a detailed observtion of each possible candidate will be 
#carried

In [154]:
df1 = toronto_merged.where(toronto_merged["1st Most Common Venue"].str.contains("Thai") | toronto_merged["2nd Most Common Venue"].str.contains("Thai") | toronto_merged["3rd Most Common Venue"].str.contains("Thai"))
df1 = df1.dropna()

In [155]:
df1

Cluster Labels                  Neighbourhood 1st Most Common Venue  \
40             1.0  High Park, The Junction South    Mexican Restaurant   
79             1.0                 Stn A PO Boxes          Cocktail Bar   

   2nd Most Common Venue 3rd Most Common Venue      4th Most Common Venue  \
40                  Café       Thai Restaurant  Cajun / Creole Restaurant   
79        Farmers Market       Thai Restaurant             Breakfast Spot   

      5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
40       Italian Restaurant                   Bar                Bakery   
79  Comfort Food Restaurant            Restaurant             Jazz Club   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
40           Flea Market   Fried Chicken Joint                  Diner   
79              Beer Bar                  Café             Food Truck   

             Borough   Latitude  Longitude  
40      West Toronto  43.661608 -79.464763  
79  Downtown Toronto  43.646435 -79.374846

In [ ]:
#Finally only 2 neighborhood were found
# To find the closest neighborhood to both of them we will use 

In [188]:
codedData = pd.get_dummies(toronto_merged)
test1 = pd.DataFrame(codedData.iloc[40,:]).transpose()
test2 = pd.DataFrame(codedData.iloc[79,:]).transpose()
codedData =codedData.drop(index =40)
codedData =codedData.drop(index =79)#fitting and transforming the desired categorical column.
codedData

Cluster Labels   Latitude  Longitude  Neighbourhood_Agincourt  \
0                1  43.794200 -79.262029                        1   
1                1  43.602414 -79.543484                        0   
2                1  43.754328 -79.442259                        0   
3                1  43.786947 -79.385975                        0   
4                1  43.733283 -79.419750                        0   
5                1  43.644771 -79.373306                        0   
6                1  43.692657 -79.264848                        0   
7                1  43.636847 -79.428191                        0   
8                1  43.662744 -79.321558                        0   
9                1  43.628947 -79.394420                        0   
10               6  43.689026 -79.453512                        0   
11               1  43.636966 -79.615819                        0   
12               1  43.773136 -79.239476                        0   
13               1  43.657952 -79.387383                        0   
14               1  43.669542 -79.422564                        0   
15               1  43.665860 -79.383160                        0   
16               1  43.781638 -79.304302                        0   
17               1  43.716316 -79.239476                        0   
18               1  43.648198 -79.379817                        0   
19               1  43.704324 -79.388790                        0   
20               1  43.712751 -79.390197                        0   
21               1  43.691116 -79.476013                        0   
22               1  43.745906 -79.352188                        0   
23               1  43.725900 -79.340923                        0   
24               1  43.757410 -79.273304                        0   
25               1  43.737473 -79.464763                        0   
26               1  43.739015 -79.506944                        0   
27               1  43.728496 -79.495697                        0   
28               1  43.761631 -79.520999                        0   
29               1  43.669005 -79.442259                        0   
30               6  43.685347 -79.338106                        0   
31               1  43.643515 -79.577201                        0   
32               1  43.778517 -79.346556                        0   
33               1  43.648429 -79.382280                        0   
34               6  43.696948 -79.411307                        0   
35               1  43.657162 -79.378937                        0   
36               1  43.709577 -79.445073                        0   
37               1  43.711112 -79.284577                        0   
38               1  43.763573 -79.188711                        0   
39               1  43.640816 -79.381752                        0   
41               1  43.803762 -79.363452                        0   
42               6  43.756303 -79.565963                        0   
43               3  43.724766 -79.532242                        0   
44               1  43.693781 -79.428191                        0   
45               1  43.668999 -79.315572                        0   
46               1  43.727929 -79.262029                        0   
47               1  43.653206 -79.400049                        0   
48               0  43.688905 -79.554724                        0   
49               1  43.718518 -79.464763                        0   
50               6  43.728020 -79.388790                        0   
51               1  43.709060 -79.363452                        0   
52               1  43.647927 -79.419750                        0   
53               6  43.806686 -79.194353                        0   
54               6  43.815252 -79.284577                        0   
55               1  43.628841 -79.520999                        0   
56               4  43.689574 -79.383160                        0   
57               1  43.605647 -79.501321                        0   
58

In [189]:
import scipy
ary1 = scipy.spatial.distance.cdist(test1, codedData, metric='euclidean')
ary2 = scipy.spatial.distance.cdist(test2, codedData, metric='euclidean')

In [196]:
min1 = ary1.argmin()
min2 = ary2.argmin()
if ary1.min() < ary2.min():
    mini = min1
    print("The closest value comes from neighborhood 40")
else:
    mini = min2
    print("The closest value comes from neighborhood 79")


The closest value comes from neighborhood 40


In [199]:
print(mini)
print("As we dropped index 40 the real index is mini -1")
mini = 61
correct = pd.DataFrame(toronto_merged.iloc[61,:]).transpose

61
As we dropped index 40 the real index is mini -1


In [200]:
correct

<bound method DataFrame.transpose of                                                      61
Cluster Labels                                        1
Neighbourhood           Northwood Park, York University
1st Most Common Venue                       Coffee Shop
2nd Most Common Venue                    Massage Studio
3rd Most Common Venue                               Bar
4th Most Common Venue              Caribbean Restaurant
5th Most Common Venue                Miscellaneous Shop
6th Most Common Venue                       Yoga Studio
7th Most Common Venue                Dim Sum Restaurant
8th Most Common Venue                 Electronics Store
9th Most Common Venue       Eastern European Restaurant
10th Most Common Venue                        Drugstore
Borough                                      North York
Latitude                                         43.768
Longitude                                      -79.4873>

<p> We therefore finally have our answer. We recommend either Northwood Park or York University as the place to open the Taiwan restaurant </p>